### Abstract
The following case study is an exercise in scraping data from a publicly available repository and cleaning the data using R. The intention is to configure a dataframe from multiple tables and prepare it for analysis. 

### Introduction
Obtaining data from publicly available sources is one of the great advantages of modern computing and networking. While in the past, it was difficult to acquire enough data to perform analytics and create models from, it is now commonplace to find freely available data with thousands and even millions of records. Easy as this data is to obtain, using it for analysis is not so easily accomplished.

For the purposes of this study, we will use data from the Cherry Blossom race that tracks results from the years 1999 to 2012. The Cherry Blossom race is an annual event that revolves around a ten-mile running race in Washington D.C. that is typically seen as a precursor to the Boston Marathon. The data is available via a separate URL for each year's race results. From a quick view of the downloaded data sets, it is apparent that data capture standards have evolved over the years, and do not follow a strict data governance policy. It is for this reason that extensive cleaning of the data will be needed in order to efficiently analyze the data.

Some of the issues that we will encounter are tables with different amounts of columns, non-standard column names, and special characters included in column names. Time formats will also need to be parsed according to their constituent parts, hours, minutes, seconds, and standardized on the minutes unit. Upon the creation of a well formatted data frame, simple graphics and statistics will be generated to prove the validity of our data cleaning methodology.

The case study follows the prompts from Nolan and Lang's, <u>Data Science in R</u> chapter 2.8, question 7. 

### Methods
The methods we will use in this study include standard R data cleaning procedures. Close examination of the source data will be used to plan the best approach for combining the different data sets into one complete data frame. Procedures for downloading data, cleaning and merging the datasets will be employed. Conversion of character strings to integers, floats, or whatever appropriate data format will be necessary to create a data frame that is ready for analysis.

When commencing this study, it was apparent that a different approach for cleaning the data was needed used for each year's worth of data. This was indeed the most time consuming portion of the study. While strategizing the best ways to go about wrangling this problematic data set, we discovered that a large part of the column number discrepancy had to do with proper names consisting of more than one word being parsed to separate columns. This parsing issue was the result of our splitting columns on white space. While splitting on white space seemed the only viable option for designating columns, the issue of proper names being split into separate columns had to be remedied.

The most comprehensive approach for fixing the multi-word proper name issue was to take add code to make sure that adjacent character fields would be merged into one column. This approach luckily works well on the Cherry Blossom data, but great care should be taken if using this technique on other data sets. It just so happens that our data set has no adjacent string fields that should belong in separate columns.


In [1]:
library(XML)
ubase = "http://www.cherryblossom.org/"
menURLs = 
  c("results/1999/cb99m.html", "results/2000/Cb003m.htm", "results/2001/oof_m.html",
    "results/2002/oofm.htm", "results/2003/CB03-M.HTM",
    "results/2004/men.htm", "results/2005/CB05-M.htm", 
    "results/2006/men.htm", "results/2007/men.htm", 
    "results/2008/men.htm", "results/2009/09cucb-M.htm",
    "results/2010/2010cucb10m-m.htm", 
    "results/2011/2011cucb10m-m.htm",
    "results/2012/2012cucb10m-m.htm")

urls = paste(ubase, menURLs, sep = "")

urls[1:3]


extractResTable =
  # takes a list of websites from the cherry blossom race
  # a list of years corresponding to the year the result is for
  # and the gender of the participant
  # Retrieve data from web site, 
  # find the preformatted text,
  # and write lines or return as a character vector.
  # returns a list of strings corrsponding to lines in the web url
  function(url = "http://www.cherryblossom.org/results/2009/09cucb-F.htm",
           year = 1999, sex = "male", file = NULL)
  {
    doc = htmlParse(url)

    if (year == 2000) {
      # Get preformatted text from 4th font element
      # The top file is ill formed so the <pre> search doesn't work.
      ff = getNodeSet(doc, "//font")
      txt = xmlValue(ff[[4]])
      els = strsplit(txt, "\r\n")[[1]]
    }
    else if (year == 2009 & sex == "male") {
      # Get preformatted text from <div class="Section1"> element
      # Each line of results is in a <pre> element
      div1 = getNodeSet(doc, "//div[@class='Section1']")
      pres = getNodeSet(div1[[1]], "//pre")
      els = sapply(pres, xmlValue)
      els = gsub("Â", " ", els)
    }
    else if (year == 1999) {
      # Get preformatted text from <pre> elements
      pres = getNodeSet(doc, "//pre")
      txt = xmlValue(pres[[1]])
      els = strsplit(txt, "\n")[[1]]   
    } 
    else {
      # Get preformatted text from <pre> elements
      pres = getNodeSet(doc, "//pre")
      txt = xmlValue(pres[[1]])
      els = strsplit(txt, "\r\n")[[1]]   
    } 
    
    if (is.null(file)) return(els)
    # Write the lines as a text file.
    writeLines(els, con = file)
  }


years = 1999:2012
menTables = mapply(extractResTable, url = urls, year = years)
names(menTables) = years
sapply(menTables, length)

#womenTables = mapply(extractResTable, url = urls, 
#                       year = years, sex = rep("female", 14))
#names(womenTables) = years
#sapply(womenTables, length)


save(menTables, file = "CBMenTextTables.rda")

Warning message:
"package 'XML' was built under R version 3.4.4"

[1] "http://www.cherryblossom.org/results/1999/cb99m.html"
[2] "http://www.cherryblossom.org/results/2000/Cb003m.htm"
[3] "http://www.cherryblossom.org/results/2001/oof_m.html"

1999 2000 2001 2002 2003 2004 2005 2006 2007 2008 2009 2010 2011 2012 
3193 3019 3627 3727 3951 4164 4335 5245 5283 5913 6659 6919 7019 7201

In [2]:
extractResTable(url = urls[11], year = 2009, sex = 'male')

[1] "  "                                                                                                                                          
   [2] "                                 Credit Union Cherry Blossom Ten Mile Run"                                                                   
   [3] "                                 Washington, DC         Sunday, April 5, 2009"                                                               
   [4] "  "                                                                                                                                          
   [5] "                                                     Official Male Results"                                                                  
   [6] "  "                                                                                                                                          
   [7] "Place Div   /Tot     Num       Name                                     Ag Hometown                         Gun Tim Net Tim   Pace   "       
   [8] "===== =========== ====== ====================== == ==================== ======= =======   ===== "                                            
   [9] "        1         1/1420             1 Ridouane Harroufi           27 Morocco                               45:56     45:56#   4:36 "        
  [10] "        2         1/62                 9 Feyisa Liesa                     19 Ethiopia                             45:58     45:58#   4:36 "  
  [11] "        3         1/1271           13 Silas Sang                         31 Kenya                                   45:59     45:59#   4:36 "
  [12] "        4         2/1420           29 Karim El Mabchour           26 Morocco                               46:00     46:00#   4:36 "         
  [13] "        5         3/1420           81 Stephen Chemlany             26 Kenya                                   46:06     46:06#   4:37 "      
  [14] "        6         1/399             83 Cosmas Koech Kimuati     23 Kenya                                   46:08     46:08#   4:37 "         
  [15] "        7         2/399             17 Philemon Terer                 24 Kenya                                   46:28     46:28#   4:39 "   
  [16] "        8         2/1271           19 Samuel Ndereba                 32 Kenya                                   46:58     46:58#   4:42 "    
  [17] "        9         4/1420             7 Kiplimo Kimutai               27 Kenya                                   47:03     47:03#   4:43 "    
  [18] "      10         1/1037           25 Lee Troop                           36 Australia                           47:43     47:43#   4:47 "    
  [19] "      11         5/1420           33 Eric Chirchir                   25 Kenya                                   47:54     47:54#   4:48 "    
  [20] "      12         3/399             23 Patrick Kipkemo Cherui 21 Kenya                                   47:56     47:56#   4:48 "            
  [21] "      13         4/399             51 Lewis Nyariki                   20 Kenya                                   47:56     47:56#   4:48 "   
  [22] "      14         6/1420           43 Jason Hartman                   28 Boulder CO                         48:03     48:03#   4:49 "         
  [23] "      15         3/1271           35 Jason Lehmkuhle               31 Minneapolis MN                 48:04     48:04#   4:49 "               
  [24] "      16         4/1271           85 Augustus Mbusya               32 Kenya                                   48:05     48:05#   4:49 "      
  [25] "      17         7/1420           79 Mike Morgan                       29 United States                   48:06     48:06#   4:49 "          
  [26] "      18         8/1420           47 Naoto Morimoto                 25 Japan                                   48:13     48:13#   4:50 "     
  [27] "      19         9/1420           45 Mitinori Takano               27 Japan                    

In [3]:
womenURLs = 
  c("results/1999/cb99f.html", "results/2000/Cb003f.htm", "results/2001/oof_f.html",
    "results/2002/ooff.htm", "results/2003/CB03-F.HTM",
    "results/2004/women.htm", "results/2005/CB05-F.htm", 
    "results/2006/women.htm", "results/2007/women.htm", 
    "results/2008/women.htm", "results/2009/09cucb-F.htm",
    "results/2010/2010cucb10m-F.htm", 
    "results/2011/2011cucb10m-F.htm",
    "results/2012/2012cucb10m-F.htm")

In [4]:
years = 1999:2012
urls = paste(ubase, womenURLs, sep = "")
urls[1:3]
womenTables = mapply(extractResTable, url = urls, year = years, sex='female')
names(womenTables) = years
sapply(womenTables, length)

[1] "http://www.cherryblossom.org/results/1999/cb99f.html"
[2] "http://www.cherryblossom.org/results/2000/Cb003f.htm"
[3] "http://www.cherryblossom.org/results/2001/oof_f.html"

1999 2000 2001 2002 2003 2004 2005 2006 2007 2008 2009 2010 2011 2012 
2359 2169 2976 3338 3547 3907 4342 5445 5699 6405 8333 8863 9038 9738

In [5]:
tail(menTables$'2009')

[1] "  6646   1271/1271       9604 John Sim                             34 Fairfax VA                     2:34:48 2:25:33   14:34 "     
[2] "  6647     161/161       18746 Kerry Kilman                     61 Rockville MD                 2:28:36 2:27:47   14:47 "          
[3] "  6648         7/8             2670 Edward Jefferson             75 Norfolk VA                     2:31:25 2:28:02   14:49 "       
[4] "  6649         8/8               264 Robert Smith                     75 Comus MD                         2:35:01 2:34:22   15:27 "
[5] "# Under USATF OPEN guideline       "                                                                                               
[6] "* Under USATF Age-Group guideline"

In [6]:

#     columns <- testData[startIndex-1]
#     columns <- columns[[1]]
#     columns <- strsplit(columns, "( \|\)\\s+{2}")[[1]]

In [7]:
stringNeighbors <- function(elems, year){
    divtot <- NA
    place <- elems[1]
    name <- ""
    age <- NA
    origin <- ""
    time <- NA
    
    nameDone <- FALSE
    temp <- ""
    for(i in 2:length(elems)){
        if(length(elems[i]) == 0){ next }
        if(grepl('/', elems[i])){ 
            divtot <- elems[i] 
            next
        }else if(grepl(':', elems[i])){
            
            origin <- temp
            time <- parse_time(elems,i,year)
            break
        }
        if(!castableToNum(elems[i])){
            if(!grepl(':', elems[i])){
                temp <- paste(temp, elems[i], sep=" ")
            }            
        }else{            
            if(!nameDone){
                if(as.numeric(elems[i]) < 130){
                    nameDone <- TRUE
                    name = temp
                    temp = ""
                }                
            }            
            age <- as.numeric(elems[i])
        }        
    }
    return(list(place,divtot,name,age,origin,time))
}
    
parse_time <- function(elems,i, year){
    switch(year,
          "1999" = return(elems[i]),
          "2000" = return(elems[i+1]),
          "2001" = return(elems[i]),
          "2002" = return(elems[i]),
          "2003" = return(elems[i+1]),
          "2004" = return(elems[i]),
          "2005" = return(elems[i]),
          "2006" = return(elems[i]),
          "2007" = return(elems[i]),
          "2008" = return(elems[i+4]),
          "2009" = return(elems[i+1]),
          "2010" = return(elems[i+3]),
          "2011" = return(elems[i+3]),
          "2012" = return(elems[i+1])
          )
}

In [8]:
columns <- c("Year","Place","Div/Tot","Name","Age","Hometown","Time")

frame_lengths <- sapply(womenTables, length)

castableToNum <- function(elem){
    suppressWarnings(!is.na(as.numeric(elem)))
}

parse_table <- function(col, year){
    testData <- strsplit(col, "'")
    startIndex <- grep( "====",testData)
    if(length(startIndex) == 0){startIndex <- 3}
    
    testData <- testData[startIndex+1:length(testData)]

    year_obs_count <- frame_lengths[year][[1]]
    cols <- list()
    for(c in  1:length(columns)){
      cols[[columns[c]]] <- character(year_obs_count)
    }
    
    line <- as.character(testData)    
    for(i in 1:year_obs_count){
        temp <- strsplit(line, "\\s+")[[i]]
        temp <- temp[-1]
        
        vals <- stringNeighbors(temp, year)
        
        cols$Year[i] <- year
        cols$Place[i] <- vals[1]
        cols$'Div/Tot'[i] <- vals[2]
        cols$Name[i] <- vals[3]
        cols$Age[i] <- vals[4]
        cols$Hometown[i] <- vals[5]
        cols$Time[i] <- vals[6]
    }
    return(cols)
}



In [9]:
## preview data
# print(womenTables$'2003'[1:30])

In [10]:
##Test individual
# parse_table(womenTables$'2003', "2003")

In [ ]:
#Get Collection
lapply(seq_along(womenTables), function(i) parse_table(womenTables[[i]], names(womenTables)[[i]]))

### Results
Creating the data frame proved challenging and required much trial and error in order to obtain a currently formatted table. Problematic was the lack of standardized data reporting formats over the course of the 13 years of the study. 

A common occurrence was the situation where we thought that the data was formatted correctly, but after reviewing the data, it was apparent that a particular year had left out a field or had used a different standard for naming a field. The only remedy for this situation was to continually fix, review, and reformat the data to create the data frame.

### Conclusion
The data used in this case study presented serious challenges to forming a consistent data frame suitable for analysis. The inconsistent naming conventions and data discrepancies were among some of the issues that had to be overcome. This challenged our ability to use R for data cleaning and in hindsight proved to be not as efficient as a pandas data frame in Python. It seems that a mixed approach of using R in conjunction with Python may be necessary in order to get the best results with the least amount of effort. All in all however, R was able to perform the functions we asked of it and allowed for this case study to be executed in accordance with the tenets of reproducible research.

The statistics generated for the data frame show that the ages change over time.